In [32]:
import pandas as pd

In [33]:
df = pd.read_csv(r"C:\Users\joao.herculano\Downloads\VENDAS_BAHIA_27_08.csv",sep=';')

In [34]:
df.head()

nf  data_venda         canal                              PDV    cod  \
0  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  52276   
1  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  49016   
2  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  50481   
3  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  52334   
4  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  50483   

                                       desc  qtd valor_unit valor_total  
0        KIT SACOLA P INST EUD 2022 C/10 VD    1       6,37        6,37  
1             ACCORDES DES BDY SPR 100ml V6    1      40,72       40,72  
2  GLAM BAT MICRO PLUMP VERMELHO UNICO 1,8g    1      24,43       24,43  
3    SOUL K/M BAT MATE VERM MODERNO V2 3,7g    1      25,19       25,19  
4    GLAM BAT MICRO PLUMP ROSADO NOBRE 1,8g    1      24,43       24,43

In [35]:
df = df.rename(columns={'cod':'SKU'})
df.head()

nf  data_venda         canal                              PDV    SKU  \
0  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  52276   
1  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  49016   
2  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  50481   
3  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  52334   
4  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  50483   

                                       desc  qtd valor_unit valor_total  
0        KIT SACOLA P INST EUD 2022 C/10 VD    1       6,37        6,37  
1             ACCORDES DES BDY SPR 100ml V6    1      40,72       40,72  
2  GLAM BAT MICRO PLUMP VERMELHO UNICO 1,8g    1      24,43       24,43  
3    SOUL K/M BAT MATE VERM MODERNO V2 3,7g    1      25,19       25,19  
4    GLAM BAT MICRO PLUMP ROSADO NOBRE 1,8g    1      24,43       24,43

In [36]:
df['pdv_tratado'] = df['PDV'].str.split('-').str[0]
df['pdv_tratado'].head()

0    20970
1    20970
2    20970
3    20970
4    20970
Name: pdv_tratado, dtype: object

In [37]:
df_marca = pd.read_csv(r"C:\Users\joao.herculano\OneDrive - GRUPO GINSENG\Documentos\CONSULTAS BANCO DE DADOS\skus e marcas 20250828.csv",sep=';')

df_marca.head()

SKU origem
0  72898    BOT
1  49586    BOT
2   5221    BOT
3  28644    BOT
4  85154    BOT

In [38]:
df = pd.merge(df,df_marca,on='SKU',how='left')

df.head()

nf  data_venda         canal                              PDV    SKU  \
0  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  52276   
1  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  49016   
2  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  50481   
3  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  52334   
4  32892  27/08/2025  Venda Direta  20970-COMERCIO-ER SAO SEBASTIAO  50483   

                                       desc  qtd valor_unit valor_total  \
0        KIT SACOLA P INST EUD 2022 C/10 VD    1       6,37        6,37   
1             ACCORDES DES BDY SPR 100ml V6    1      40,72       40,72   
2  GLAM BAT MICRO PLUMP VERMELHO UNICO 1,8g    1      24,43       24,43   
3    SOUL K/M BAT MATE VERM MODERNO V2 3,7g    1      25,19       25,19   
4    GLAM BAT MICRO PLUMP ROSADO NOBRE 1,8g    1      24,43       24,43   

  pdv_tratado origem  
0       20970    EUD  
1       20970    BOT  
2       20970    EUD  
3       20970    EUD  
4       20970    EUD

In [40]:

df['valor_unit'] = df['valor_unit'].str.replace(',','.')

df['valor_unit'] = df['valor_unit'].astype(float)


In [41]:
df['valor_total'] = df['valor_unit']*df['qtd']

df.dtypes

nf               int64
data_venda      object
canal           object
PDV             object
SKU              int64
desc            object
qtd              int64
valor_unit     float64
valor_total    float64
pdv_tratado     object
origem          object
dtype: object

In [43]:
df_agg_marca = df.groupby(['nf','pdv_tratado','origem'])['valor_total'].sum().reset_index().sort_values('nf')
df_agg_marca

nf pdv_tratado origem  valor_total
0       1367       24293    BOT       225.16
1       1368       24293    BOT      2310.04
2       1369       24293    BOT      1033.93
3       1369       24293    EUD        67.82
4       1370       24293    BOT       441.82
...      ...         ...    ...          ...
4236  324225       23711    BOT       216.80
4237  324226       23711    BOT       267.40
4238  324227       23711    BOT      7724.42
4239  324227       23711    EUD      7332.19
4240  324227       23711    QDB        31.36

[4241 rows x 4 columns]

In [45]:
caminho = r'C:\Users\joao.herculano\Documents\df_agg_vendaBA.xlsx'

with pd.ExcelWriter(caminho, engine='xlsxwriter') as writer:
    df.to_excel(writer, sheet_name='df', index=False)
    df_agg_marca.to_excel(writer, sheet_name='df_agg_marca', index=False)